In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import logging
import os
import custom_graphgym  # noqa, register custom modules
import torch
from pytorch_lightning import seed_everything
from torch_geometric.graphgym.cmd_args import parse_args
from torch_geometric.graphgym.config import (
    cfg,
    dump_cfg,
    load_cfg,
    set_out_dir,
    set_run_dir,
)
from torch_geometric.graphgym.logger import set_printing
from torch_geometric.graphgym.model_builder import create_model
from torch_geometric.graphgym.train import GraphGymDataModule, train
from torch_geometric.graphgym.utils.agg_runs import agg_runs
from torch_geometric.graphgym.utils.comp_budget import params_count
from torch_geometric.graphgym.utils.device import auto_select_device
import pandas as pd

In [4]:
from torch_geometric.graphgym import register

In [5]:
import argparse

class NotebookArgParser:
    def __init__(self, args_str):
        self.args = self.parse_args(args_str)

    def parse_args(self, args_str):
        parser = argparse.ArgumentParser(description='GraphGym')

        # Add command-line arguments
        parser.add_argument('--cfg',
                            dest='cfg_file',
                            type=str,
                            required=True,
                            help='The configuration file path.')
        parser.add_argument('--repeat',
                            type=int,
                            default=1,
                            help='The number of repeated jobs.')
        parser.add_argument('--mark_done',
                            action='store_true',
                            help='Mark yaml as done after a job has finished.')
        parser.add_argument('opts',
                            default=None,
                            nargs=argparse.REMAINDER,
                            help='See graphgym/config.py for remaining options.')

        # Parse the command-line arguments
        args = parser.parse_args(args_str)

        return args

In [6]:
# Emulate command-line arguments using input cells
command = "python main_pyg.py --cfg ./configs/pyg/ecoli_optuned_static.yaml --repeat 3"
args_str = command.split()[2:]
args_str


['--cfg', './configs/pyg/ecoli_optuned_static.yaml', '--repeat', '3']

In [7]:
# Create a NotebookArgParser instance
notebook_parser = NotebookArgParser(args_str)

# Access parsed arguments
args = notebook_parser.args
print("Parsed Arguments:")
print(f"Configuration File: {args.cfg_file}")
print(f"Repeat: {args.repeat}")
print(f"Mark Done: {args.mark_done}")
print(f"Remaining Options: {args.opts}")

Parsed Arguments:
Configuration File: ./configs/pyg/ecoli_optuned_static.yaml
Repeat: 3
Mark Done: False
Remaining Options: []


# Optuna

In [1]:
import optuna
# Load the study
study=optuna.load_study(study_name='grn-temporal-convergence-large-set',
                  storage='sqlite:///grn.db')

/home/stu13/s18/lb9849/miniconda3/envs/pyg/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:
cutoff = 0.78
trials = [t for t in study.trials if t.values and t.values[0] > cutoff]
#sort trials by the performance value
trials = sorted(trials, key=lambda t: t.values[0], reverse=True)


In [7]:
[t.values[0] for t in trials] 

[0.8938999772071838,
 0.8938999772071838,
 0.8550000190734863,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8549000024795532,
 0.8511999845

In [9]:
df_trials = pd.DataFrame(trials)
df_trials = df_trials.drop_duplicates()

In [10]:
df_trials

base_lr  layers_mp  max_epoch  layers_pre_mp  layers_post_mp  dropout  \
0      0.001          0        200              1               1     0.05   
1      0.001          0        200              1               1     0.05   
8      0.001          0        200              1               1     0.05   
13     0.001          0        200              1               1     0.05   
22     0.001          0        200              1               1     0.05   
24     0.001          0        200              1               1     0.05   
39     0.001          0        200              1               1     0.05   
71     0.001          0        200              1               1     0.05   
73     0.001          0        200              1               1     0.05   
74     0.001          0        200              1               1     0.05   
94     0.001          0        200              1               1     0.05   
96     0.001          0        200              1               1     0.05   
111    0.001          0        200              1               1     0.10   
121    0.001          0        200              1               1     0.05   
123    0.001          0        200              1               1     0.05   
126    0.001          3        200              1               1     0.05   
130    0.001          0        200              1               2     0.05   
139    0.001          0        200              3               1     0.10   
140    0.001          0        200              3               1     0.10   
141    0.001          0        200              3               1     0.10   
148    0.001          0        200              3               1     0.10   
149    0.001          0        200              3               1     0.10   
150    0.001          0        200              3               1     0.10   
154    0.001          0        200              3               1     0.10   
162    0.001          0        200              3               1     0.10   
182    0.001          0        200              3               1     0.10   
196    0.001          0        200              3               2     0.10   
210    0.001          0        200              3               1     0.10   
233    0.001          0        200              3               1     0.10   
236    0.001          0        200              3               1     0.10   
237    0.001          0        200              3               1     0.10   
245    0.001          0        200              3               1     0.10   
247    0.001          0        200              3               1     0.10   
250    0.001          0        200              3               1     0.10   
251    0.001          0        200              3               1     0.10   
252    0.001          0        200              2               1     0.10   
253    0.001          0        200              3               1     0.10   
254    0.001          0        200              3               1     0.10   
268    0.001          0        200              3               1     0.10   
269    0.001          0        200              3               1     0.10   
270    0.001          0        200              3               1     0.10   
287    0.001          2        200              3               1     0.10   
290    0.001          0        200              2               1     0.10   
292    0.001          0        200              2               1     0.10   
295    0.001          0        200              3               2     0.10   
298    0.001          3        200              2               1     0.10   
299    0.001          3        200              2               1     0.20   
300    0.001          0        200              2               1     0.20   
301    0.001          2        200              2               1     0.10   
302    0.001          3        200              2               1     0.10   
307    0.001          3    

In [11]:

# Group by all columns except 'seed' and aggregate the 'seed' column into a list
grouped_df = df_trials.groupby(df_trials.columns.difference(['seed']).tolist(), as_index=False)['seed'].agg(list)

unique_exp = grouped_df.to_dict('records') # a list of dictionary with experiments and seeds

unique_exp

[{'act': 'prelu',
  'agg': 'mean',
  'base_lr': 0.001,
  'dim_inner': 8,
  'dropout': 0.2,
  'keep_edge': 0.5,
  'layer_type': 'gatconv',
  'layers_mp': 2,
  'layers_post_mp': 2,
  'layers_pre_mp': 2,
  'max_epoch': 200,
  'scheduler': 'cos',
  'stage_type': 'skipsum',
  'weight_decay': 5e-05,
  'seed': [29]},
 {'act': 'relu',
  'agg': 'add',
  'base_lr': 0.001,
  'dim_inner': 8,
  'dropout': 0.05,
  'keep_edge': 0.0,
  'layer_type': 'gcnconv',
  'layers_mp': 0,
  'layers_post_mp': 1,
  'layers_pre_mp': 1,
  'max_epoch': 200,
  'scheduler': 'cos',
  'stage_type': 'skipconcat',
  'weight_decay': 5e-05,
  'seed': [42]},
 {'act': 'relu',
  'agg': 'add',
  'base_lr': 0.001,
  'dim_inner': 8,
  'dropout': 0.05,
  'keep_edge': 0.0,
  'layer_type': 'gcnconv',
  'layers_mp': 0,
  'layers_post_mp': 1,
  'layers_pre_mp': 1,
  'max_epoch': 200,
  'scheduler': 'cos',
  'stage_type': 'skipconcat',
  'weight_decay': 0.0005,
  'seed': [41, 42]},
 {'act': 'relu',
  'agg': 'add',
  'base_lr': 0.001,
  

In [12]:
len(unique_exp)

37

In [13]:
stem = {'base_lr': cfg.optim,
        'layers_mp': cfg.gnn,
        'max_epoch': cfg.optim,
        'layers_pre_mp': cfg.gnn,
        'layers_post_mp': cfg.gnn,
        'dropout': cfg.gnn,
        'act': cfg.gnn,
        'layer_type': cfg.gnn,
        'stage_type': cfg.gnn,
        'agg': cfg.gnn,
        'keep_edge': cfg.gnn,
        'dim_inner': cfg.gnn,
        'weight_decay': cfg.optim,
        'scheduler': cfg.optim,
        'seed': cfg}

In [14]:
os.environ["CUDA_VISIBLE_DEVICES"] = "6"
# Load config file
load_cfg(cfg, args)
set_out_dir(cfg.out_dir, args.cfg_file)
# Set Pytorch environment
dump_cfg(cfg)
set_printing()
auto_select_device() # if not set in the yaml config, set to cuda accelerator if available and single device
# Set machine learning pipeline
cfg.share.dim_out = 1
cfg.share.num_splits = 3

In [15]:
from pytorch_lightning import seed_everything

metrics = []
for exp_id, exp_param_set in enumerate(unique_exp[:10]):
    for seed in exp_param_set['seed']:
        set_run_dir(cfg.out_dir, f'{exp_id}_{seed}')
        for key, val in exp_param_set.items(): # update the parameters
            if key == 'seed':
                stem[key][key]= seed    
            else:
                stem[key][key]= val
        print(f'setting the seed:{cfg.seed}')
        seed_everything(cfg.seed, workers=True)
        datamodule = register.train_dict["CustomGraphGymDataModule"](split_type = cfg.dataset.split_type)
        model = create_model()
        cfg.params = params_count(model)
        logging.info('Num parameters: %s', cfg.params)
        # Train model using PyTorch Lightning Trainer
        val_metric = register.train_dict["train_optuna"](model, datamodule, logger=True)
        metrics.append((exp_param_set, val_metric))

Seed set to 29


setting the seed:29
DOWNLOADING CUSTOM DATASET LOADER


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'makedirs' is deprecated, use 'os.makedirs(path, exist_ok=True)' instead
  warnings.warn(out)
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/dataset.py:242: UserWarning: The `pre_transform` argument differs from the one used in the pre-processed version of this dataset. If you want to make use of another pre-processing technique, pass `force_reload=True` explicitly to reload the dataset.
  warnings.warn(
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/in_memory_dataset.py:301: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.

The number of splits is defined by the user
Positive edges 373
Positive edges 307
Negative edges 307
Positive edges 180
Negative edges 180
Positive edges 172
Negative edges 172
resetting share dim in for GNN model to: 2608


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


...

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [6]


Testing DataLoader 1: 100%|██████████| 1/1 [00:00<00:00, 107.86it/s]test_split_0: {'epoch': 200, 'loss': 0.691, 'lr': 0.0, 'params': 21088, 'time_iter': 0.0745, 'accuracy': 0.5028, 'precision': 0.5556, 'recall': 0.0278, 'f1': 0.0529, 'auc': 0.7779, 'aupr': 0.7244}
test_split_1: {'epoch': 200, 'loss': 0.6755, 'lr': 0.0, 'params': 21088, 'time_iter': 0.4842, 'accuracy': 0.5262, 'precision': 0.8462, 'recall': 0.064, 'f1': 0.1189, 'auc': 0.7363, 'aupr': 0.7097}
Testing DataLoader 1: 100%|██████████| 1/1 [00:00<00:00, 15.55it/s] 


Seed set to 8


setting the seed:8
DOWNLOADING CUSTOM DATASET LOADER


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'makedirs' is deprecated, use 'os.makedirs(path, exist_ok=True)' instead
  warnings.warn(out)


In [19]:
metrics=[]

print(trial['seed'])
set_run_dir(cfg.out_dir, trial['seed'])
for key, val in trial.items(): # update the parameters
    stem[key][key]= val
seed_everything(cfg.seed, workers=True)
datamodule = register.train_dict["CustomGraphGymDataModule"](split_type = cfg.dataset.split_type)
model = create_model()
cfg.params = params_count(model)
logging.info('Num parameters: %s', cfg.params)
# Train model using PyTorch Lightning Trainer
val_metric = register.train_dict["train_optuna"](model, datamodule, logger=True)
metrics.append(val_metric)

Seed set to 41


41
DOWNLOADING CUSTOM DATASET LOADER


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'makedirs' is deprecated, use 'os.makedirs(path, exist_ok=True)' instead
  warnings.warn(out)
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/dataset.py:242: UserWarning: The `pre_transform` argument differs from the one used in the pre-processed version of this dataset. If you want to make use of another pre-processing technique, pass `force_reload=True` explicitly to reload the dataset.
  warnings.warn(
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/in_memory_dataset.py:301: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.

The number of splits is defined by the user
Positive edges 373
Positive edges 307
Negative edges 307
Positive edges 180
Negative edges 180
Positive edges 172
Negative edges 172
resetting share dim in for GNN model to: 2608
INITIALIZING NEW CUSTOM EDGE HEAD


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


...

Epoch 25: 100%|██████████| 1/1 [00:00<00:00,  2.77it/s, v_num=0, val_accuracy=0.500, val_precision=0.000, val_recall=0.000, val_f1=0.000, val_auc=0.864, val_aupr=0.854]

/home/stu13/s18/lb9849/miniconda3/envs/pyg/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/stu13/s18/lb9849/miniconda3/envs/pyg/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


train: {'epoch': 25, 'eta': 15.736, 'loss': 0.6365, 'lr': 0.001, 'params': 20944, 'time_iter': 0.0798, 'accuracy': 0.5027, 'precision': 1.0, 'recall': 0.0054, 'f1': 0.0107, 'auc': 0.982, 'aupr': 0.9842}
Epoch 199: 100%|██████████| 1/1 [00:00<00:00,  2.00it/s, v_num=0, val_accuracy=0.557, val_precision=0.927, val_recall=0.124, val_f1=0.218, val_auc=0.841, val_aupr=0.835]

`Trainer.fit` stopped: `max_epochs=200` reached.


Epoch 199: 100%|██████████| 1/1 [00:00<00:00,  1.74it/s, v_num=0, val_accuracy=0.557, val_precision=0.927, val_recall=0.124, val_f1=0.218, val_auc=0.841, val_aupr=0.835]


In [20]:
metrics

[tensor(0.8349)]

# Training

In [9]:
# Load config file
load_cfg(cfg, args)
#set_out_dir(cfg.out_dir, args.cfg_file)
# Set Pytorch environment
torch.set_num_threads(cfg.num_threads)
#dump_cfg(cfg)

In [12]:
datamodule_static = register.train_dict["CustomGraphGymDataModule"]()

DOWNLOADING CUSTOM DATASET LOADER


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'makedirs' is deprecated, use 'os.makedirs(path, exist_ok=True)' instead
  warnings.warn(out)
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/dataset.py:242: UserWarning: The `pre_transform` argument differs from the one used in the pre-processed version of this dataset. If you want to make use of another pre-processing technique, pass `force_reload=True` explicitly to reload the dataset.
  warnings.warn(
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/in_memory_dataset.py:301: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.

The number of splits is defined by the user
resetting share dim in for GNN model to: 2608


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [13]:
datamodule_static._get_split_statistics()

[            # MPP edges  # label pos edges  # label neg edges
 train              5653               5653                  0
 val                5653                706                706
 test               6359                706                706
 final_test         6359                347                347]

In [15]:
datamodule_temp = register.train_dict["CustomGraphGymDataModule"](split_type='temporal')

DOWNLOADING CUSTOM DATASET LOADER


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'makedirs' is deprecated, use 'os.makedirs(path, exist_ok=True)' instead
  warnings.warn(out)
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/dataset.py:242: UserWarning: The `pre_transform` argument differs from the one used in the pre-processed version of this dataset. If you want to make use of another pre-processing technique, pass `force_reload=True` explicitly to reload the dataset.
  warnings.warn(
/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/in_memory_dataset.py:301: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.

The number of splits is defined by the user
Positive edges 373
Positive edges 307
Negative edges 307
Positive edges 180
Negative edges 180
Positive edges 172
Negative edges 172
resetting share dim in for GNN model to: 2608


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [16]:
datamodule_temp._get_split_statistics()

[            # MPP edges  # label pos edges  # label neg edges
 train              6647                373                  0
 val                6788                307                307
 test               7065                180                180
 final_test         7065                172                172]

In [ ]:


for i in range(args.repeat):
    set_run_dir(cfg.out_dir, i)
    set_printing()
    # Set configurations for each run
    cfg.seed = cfg.seed + 1
    seed_everything(cfg.seed)
    auto_select_device() # if not set in the yaml config, set to cuda accelerator if available and single device
    # Set machine learning pipeline
    datamodule = register.train_dict["CustomGraphGymDataModule"]()
    cfg.share.dim_out = 1 # TODO fix this bug, that happend in set_dataset_info because dataset._data.y might have node labels (not edge labels)
    cfg.share.num_splits = 3 # TODO fix this bug
    model = create_model()
    # Print model info
    logging.info(model)
    logging.info(cfg)
    cfg.params = params_count(model)
    logging.info('Num parameters: %s', cfg.params)
    # Call the custom training function
    register.train_dict["train_pl"](model, datamodule, logger=True)
    #train(model, datamodule, logger=True)

DOWNLOADING CUSTOM DATASET LOADER
INITIALIZING NEW CUSTOM EDGE HEAD


/home/stu13/s18/lb9849/BioCompute/pytorch_geometric/torch_geometric/data/in_memory_dataset.py:301: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.warn(msg)


GraphGymModule(
  (model): GNN(
    (encoder): FeatureEncoder()
    (mp): GNNStackStage(
      (layer0): GeneralLayer(
        (layer): GCNConv(
          (model): GCNConv(1433, 64)
        )
        (post_layer): Sequential(
          (0): ReLU()
        )
      )
      (layer1): GeneralLayer(
        (layer): GCNConv(
          (model): GCNConv(64, 64)
        )
        (post_layer): Sequential(
          (0): ReLU()
        )
      )
    )
    (post_mp): ExampleGNNEdgeHead(
      (layer_post_mp): MLP(
        (model): Sequential(
          (0): Linear(
            (model): Linear(64, 64, bias=True)
          )
        )
      )
    )
  )
)
accelerator: cuda
benchmark: False
bn:
  eps: 1e-05
  mom: 0.1
cfg_dest: config.yaml
custom_metrics: []
dataset:
  cache_load: False
  cache_save: False
  dir: ./datasets
  edge_dim: 128
  edge_encoder: False
  edge_encoder_bn: True
  edge_encoder_name: Bond
  edge_message_ratio: 0.8
  edge_negative_sampling_ratio: 1.0
  edge_train_mode: all
  enc

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
Missing logger folder: results/link_predict_debug/example_link_debug/lightning_logs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3,4,5,6,7,8,9]

  | Name  | Type | Params
-------------------------------
0 | model | GNN  | 100 K 
-------------------------------
100 K     Trainable params
0         Non-trainable params
100 K     Total params
0.400     Total estimated model params size (MB)


Sanity Checking DataLoader 0:   0%|          | 0/1 [00:00<?, ?it/s]

...

Epoch 399: 100%|██████████| 1/1 [00:00<00:00,  3.77it/s, v_num=2]

`Trainer.fit` stopped: `max_epochs=400` reached.


Epoch 399: 100%|██████████| 1/1 [00:00<00:00,  2.50it/s, v_num=2]


LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3,4,5,6,7,8,9]
/home/stu13/s18/lb9849/miniconda3/envs/pyg/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:441: The 'test_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=23` in the `DataLoader` to improve performance.


Testing DataLoader 0: 100%|██████████| 1/1 [00:00<00:00, 19.43it/s] 
